In [54]:
import pathlib
import numpy as np
import tensorflow as tf
import sys
import pandas as pd
sys.path.append("..")
from utils.preprocess import *
from sklearn.preprocessing import StandardScaler, LabelEncoder
from tensorflow.keras.utils import to_categorical
from sklearn.model_selection import train_test_split


In [55]:
# class ExportModel(tf.Module):
#   def __init__(self, model):
#     self.model = model

#     # Accept either a string-filename or a batch of waveforms.
#     # YOu could add additional signatures for a single wave, or a ragged-batch. 
#     self.__call__.get_concrete_function(
#         x=tf.TensorSpec(shape=(), dtype=tf.string))
#     self.__call__.get_concrete_function(
#        x=tf.TensorSpec(shape=[None, 16000], dtype=tf.float32))


#   @tf.function
#   def __call__(self, x):
#     # If they pass a string, load the file and decode it. 
#     if x.dtype == tf.string:
#       x = tf.io.read_file(x)
#       x, _ = tf.audio.decode_wav(x, desired_channels=1, desired_samples=16000,)
#       x = tf.squeeze(x, axis=-1)
#       x = x[tf.newaxis, :]

#     x = get_spectrogram(x)  
#     result = self.model(x, training=False)

#     class_ids = tf.argmax(result, axis=-1)
#     class_names = tf.gather(label_names, class_ids)
#     return {'predictions':result,
#             'class_ids': class_ids,
#             'class_names': class_names}

In [56]:
# def get_spectrogram(waveform):
#   # Convert the waveform to a spectrogram via a STFT.
#   spectrogram = tf.signal.stft(
#       waveform, frame_length=255, frame_step=128)
#   # Obtain the magnitude of the STFT.
#   spectrogram = tf.abs(spectrogram)
#   # Add a `channels` dimension, so that the spectrogram can be used
#   # as image-like input data with convolution layers (which expect
#   # shape (`batch_size`, `height`, `width`, `channels`).
#   spectrogram = spectrogram[..., tf.newaxis]
#   return spectrogram

# def preprocess(x):
#     x = tf.io.read_file(x)
#     x, _ = tf.audio.decode_wav(x, desired_channels=1, desired_samples=16000,)
#     x = tf.squeeze(x, axis=-1)
#     x = x[tf.newaxis, :]

#     x = get_spectrogram(x)  
#     return x

In [57]:
# export = ExportModel(model)
# export(tf.constant(str(data_dir/'no/01bb6a2a_nohash_0.wav')))

In [58]:
# DATASET_PATH = 'data/mini_speech_commands'

# data_dir = pathlib.Path(DATASET_PATH)

In [59]:
import os

In [60]:
input_directory = "../assets/Respeck"

data_list = []
label_list = []
total_rows = 0

all_occu = {}

for folder_name in os.listdir(input_directory):
    folder_path = os.path.join(input_directory, folder_name)
    if folder_name == ".DS_Store":
        continue
    for file in os.listdir(folder_path):
        if file.endswith(".csv") and "unprocessed" not in file:
            
            filename = os.path.join(folder_path, file)
            label, _, _ = extract_activity_and_status(filename)
            if label not in all_occu:
                all_occu["label"] = 1
                all_occu["directory"] = [filename]
            else:
                all_occu["label"] += 1
                all_occu["directory"].append(filename)
            df = pd.read_csv(filename, usecols=[2,3,4])

            # Determine the number of rows to take from this file
            rows_to_take = min(50 - total_rows, len(df))
            
            # Update the df to only contain the necessary rows and update our counter
            df = df.head(rows_to_take)
            label_list.append(label)
            data_list.append(df)

# all_data = pd.concat(data_list, ignore_index=True)
print(data_list)

[     accel_x   accel_y   accel_z
0  -0.791260  0.098816 -0.594299
1  -0.790527  0.098816 -0.593567
2  -0.797607  0.092957 -0.598450
3  -0.773438  0.099792 -0.585266
4  -0.800293  0.096375 -0.594055
5  -0.783447  0.102478 -0.594543
6  -0.793945  0.090027 -0.593811
7  -0.790771  0.095642 -0.586975
8  -0.779785  0.085144 -0.633606
9  -0.791260  0.095642 -0.566711
10 -0.770264  0.101257 -0.608215
11 -0.785889  0.102478 -0.588684
12 -0.791016  0.107117 -0.598206
13 -0.786377  0.111267 -0.581848
14 -0.799561  0.112244 -0.577454
15 -0.788818  0.100525 -0.583069
16 -0.792480  0.112732 -0.596741
17 -0.797119  0.096375 -0.573547
18 -0.789062  0.115173 -0.583557
19 -0.802979  0.110779 -0.575745
20 -0.788330  0.113953 -0.589905
21 -0.780273  0.104919 -0.589905
22 -0.790771  0.103455 -0.592346
23 -0.788574  0.105408 -0.594299
24 -0.782227  0.103455 -0.586487
25 -0.805664  0.111511 -0.596741
26 -0.766357  0.109558 -0.590149
27 -0.802979  0.103699 -0.594055
28 -0.793457  0.117859 -0.577698
29 -0.802

In [61]:

# Normalizing sensor readings
scaler = StandardScaler()

sensor_columns = ['accel_x', 'accel_y', 'accel_z']

scaler.fit(data_list[0][sensor_columns])

for i in range(len(data_list)):
    data_list[i][sensor_columns] = scaler.transform(data_list[i][sensor_columns])


In [62]:
# Assuming your data_list and label_list are predefined
# Convert data and labels to numpy arrays
X = np.array([df.values for df in data_list])
X = np.stack(X)
y = LabelEncoder().fit_transform(label_list)

# Convert X to float32 and y to categorical (for softmax)
X = X.astype('float32')
y = to_categorical(y)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


In [63]:
X_train.shape

(1619, 50, 3)

In [73]:
np.array([X_train[0]]).shape

(1, 50, 3)

In [75]:
np.array([X_train[0]])

array([[[114.48313 , -22.995321, -35.835392],
        [111.93242 , -25.136877, -37.43091 ],
        [108.946915, -27.421206, -35.635952],
        [108.10634 , -27.09997 , -35.30355 ],
        [105.90345 , -27.671053, -37.142834],
        [105.555626, -28.527676, -35.547314],
        [105.2078  , -28.527676, -36.478035],
        [106.13533 , -28.491983, -36.921234],
        [105.58461 , -27.885208, -36.699635],
        [108.077354, -27.63536 , -33.796673],
        [112.51212 , -27.63536 , -40.511154],
        [112.25125 , -26.564583, -33.619392],
        [112.62807 , -26.778738, -36.345074],
        [110.91792 , -27.63536 , -33.88531 ],
        [108.28025 , -28.706139, -38.272995],
        [104.193306, -30.954773, -37.43091 ],
        [101.93245 , -32.061245, -38.339474],
        [101.00491 , -32.346786, -35.370033],
        [100.59911 , -31.026157, -36.16779 ],
        [ 99.52666 , -31.59724 , -36.65531 ],
        [ 99.55564 , -31.525854, -36.699635],
        [ 99.265785, -31.311699, -

In [78]:
dataReceived = [
[[0.03955078125, 0.01141357421875, 1.08978271484375]],
[[0.0234375, -0.05426025390625, 1.06463623046875]],
[[0.03759765625, 0.01800537109375, 1.07025146484375]],
[[0.012939453125, -0.01910400390625, 1.06512451171875]],
[[0.0185546875, -0.01129150390625, 1.05511474609375]],
[[0.020263671875, -0.00030517578125, 1.03118896484375]],
[[0.022705078125, -0.01495361328125, 1.06243896484375]],
[[0.025634765625, 0.00140380859375, 1.02947998046875]],
[[0.0380859375, 0.02703857421875, 1.05169677734375]],
[[0.02587890625, -0.06207275390625, 1.07708740234375]],
[[0.081787109375, -0.00689697265625, 1.04388427734375]],
[[0.032470703125, -0.05938720703125, 1.07977294921875]],
[[-0.051025390625, 0.01141357421875, 1.12884521484375]],
[[0.03564453125, -0.00640869140625, 1.10614013671875]],
[[-0.02734375, -0.04083251953125, 1.06414794921875]],
[[0.006591796875, -0.01031494140625, 0.97943115234375]],
[[0.001953125, -0.00469970703125, 1.05950927734375]],
[[-0.01123046875, -0.00909423828125, 1.06048583984375]],
[[0.0576171875, 0.00872802734375, 1.09027099609375]],
[[0.03466796875, 0.08709716796875, 1.12469482421875]],
[[0.095458984375, 0.08514404296875, 1.04388427734375]],
[[0.082275390625, 0.01165771484375, 1.11370849609375]],
[[0.5009765625, 0.35052490234375, 1.52484130859375]],
[[0.040771484375, -0.09429931640625, 1.03900146484375]],
[[-0.00390625, -0.20050048828125, 0.83489990234375]],
[[-0.00732421875, -0.00592041015625, 0.00213623046875]],
[[0.00537109375, 0.17181396484375, 1.13568115234375]],
[[-0.008056640625, 0.03851318359375, 1.08831787109375]],
[[-0.014892578125, 0.01019287109375, 1.07342529296875]],
[[-0.01025390625, 0.00189208984375, 1.06854248046875]],
[[-0.0107421875, 0.00091552734375, 1.07904052734375]],
[[-0.01416015625, -0.00006103515625, 1.06683349609375]],
[[-0.018310546875, -0.00762939453125, 1.07147216796875]],
[[-0.0126953125, -0.00372314453125, 1.07098388671875]],
[[-0.0146484375, 0.00823974609375, 1.06903076171875]],
[[-0.016357421875, -0.00689697265625, 1.07440185546875]],
[[-0.01708984375, -0.00250244140625, 1.06781005859375]],
[[-0.0166015625, 0.00286865234375, 1.06903076171875]],
[[-0.013427734375, -0.01251220703125, 1.06707763671875]],
[[-0.016357421875, -0.00616455078125, 1.07293701171875]],
[[-0.0126953125, 0.00286865234375, 1.07000732421875]],
[[-0.01416015625, -0.00347900390625, 1.06365966796875]],
[[-0.01806640625, 0.00018310546875, 1.06878662109375]],
[[-0.017333984375, -0.00616455078125, 1.06610107421875]],
[[-0.00830078125, 0.00042724609375, 1.06951904296875]],
[[-0.012939453125, -0.00201416015625, 1.07000732421875]],
[[-0.022705078125, 0.00115966796875, 1.07440185546875]],
[[-0.017333984375, -0.00250244140625, 1.06854248046875]],
[[-0.013671875, -0.00494384765625, 1.07415771484375]],
[[-0.0185546875, -0.00494384765625, 1.07171630859375]]]

In [79]:
dataReceived.shape

AttributeError: 'list' object has no attribute 'shape'

In [91]:
test_list = [[0, 0, -1]] * 50

In [92]:
import tensorflow as tf
import numpy as np

# Load the TFLite model and allocate tensors.
interpreter = tf.lite.Interpreter(model_path="../exported_models/model_online.tflite")
interpreter.allocate_tensors()

# Get input and output tensors.
input_details = interpreter.get_input_details()
output_details = interpreter.get_output_details()

# Load and preprocess the audio file
# file_path = str(data_dir/'no/01bb6a2a_nohash_0.wav')
# data = preprocess(file_path)

# Ensure the input data is the correct shape and type
input_shape = input_details[0]['shape']
print(input_details)
input_data = np.array(test_list, dtype=input_details[0]['dtype']).reshape(input_shape)

# Set the tensor and invoke the interpreter
interpreter.set_tensor(input_details[0]['index'], np.array([X_train[0]]))
interpreter.invoke()

# Get the output tensor
output_data = interpreter.get_tensor(output_details[0]['index'])
print(output_data)

max_result = np.argmax(output_data)

[{'name': 'serving_default_conv1d_24_input:0', 'index': 0, 'shape': array([ 1, 50,  3], dtype=int32), 'shape_signature': array([-1, 50,  3], dtype=int32), 'dtype': <class 'numpy.float32'>, 'quantization': (0.0, 0), 'quantization_parameters': {'scales': array([], dtype=float32), 'zero_points': array([], dtype=int32), 'quantized_dimension': 0}, 'sparsity_parameters': {}}]
[[6.96734380e-12 5.70273212e-12 9.16933418e-10 2.27137003e-03
  9.97715473e-01 1.22741385e-05 8.47473018e-07 1.23031724e-10
  1.53892486e-14 3.39876904e-15 3.85271565e-10 4.07600993e-08]]


In [93]:
print(label_list[max_result])

lying down back
